In [11]:
import importlib

In [18]:
import pandas as pd

pd.set_option("display.max_colwidth", 0)

In [47]:
import src.embedding as embedding
import src.storage as storage
from src.storage import ArXivData
from src.cleaning import TextCleaner
from src.embedding import Embedder
from sentence_transformers import util

importlib.reload(embedding)
importlib.reload(storage)

<module 'storage' from 'c:\\Users\\Leems\\Desktop\\Coding\\Projects\\Fritz\\storage.py'>

In [39]:
## Load library
library_path = "./data/APSP_50.feather"
path_to_library_embeddings = "./data/allenai-specter_APSP_50_embeddings.feather"

library = ArXivData()
library.load_from_feather(library_path)

In [40]:
## Prepare the Library

cleaner = TextCleaner()
embedder = Embedder()

clean_library = cleaner.transform(library)
prepped_library = embedder.transform(
    X=clean_library, load_from_file=True, path_to_embeddings=path_to_library_embeddings
)

In [48]:
## retrieve and pre-process the input

input_id = "1602.00730"

## create query string

id_list = [input_id]

input_article = ArXivData()
input_article.load_from_id_list(id_list=id_list)

In [49]:
## Clean and process the input

clean_input_article = cleaner.transform(input_article)
prepped_input_article = embedder.transform(
    X=clean_input_article,
    model_name="allenai-specter",
    path_to_embeddings="./data/input_embedding.feather",
)

c:\Users\Leems\Desktop\Coding\Projects\Fritz\cleaning.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X.metadata.msc_tags[X.metadata.msc_tags.notna()] = X.metadata.msc_tags[
Batches: 100%|██████████| 1/1 [00:00<00:00,  4.39it/s]


In [55]:
## Perform the search and return the closest matches

matches = util.semantic_search(
    query_embeddings=prepped_input_article.embeddings,
    corpus_embeddings=prepped_library.embeddings,
    top_k=5,
)

In [57]:
indices = [dict["corpus_id"] for dict in matches[0]]

In [59]:
indices

[38787, 39127, 9786, 49609, 14857]

In [60]:
## Retrieve indices

prepped_library._returned_metadata.iloc[indices]

title  \
38787  C-infinity Scaling Asymptotics for the Spectral Function of the Laplacian                                  
39127  Scaling Limit for the Kernel of the Spectral Projector and Remainder Estimates in the Pointwise Weyl Law   
9786   A logarithmic improvement in the two-point Weyl law for manifolds without conjugate points                 
49609  The blowup along the diagonal of the spectral function of the Laplacian                                    
14857  Growth of high LATEX  norms for eigenfunctions: an application of geodesic beams                           

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     abstract  \
38787  This article concerns new off-diagonal estimates on the remainder and its derivatives in the pointwise Weyl law on a compact n-dimensional Riemannian manifold. As an application, we prove that near any non self-focal point, the scaling limit of the spectral projector of the Laplacian onto frequency windows of constant size is a normalized Bessel function depending only on n.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
39127  Let (M, g) be a compact smooth Riemannian manifold. We obtain new off-diagonal estimates as {ambda} tend to infinity for the remainder in the pointwise Weyl Law for the kernel of the spectral projector of the Laplacian onto functions with frequency at most {ambda}. A corollary is that, when rescaled around a non self-focal point, the kernel of the spectral projector onto the frequency interval (ambda, ambda + 1] has a universal scaling limit as {ambda} goes to infinity (depending only on the dimension of M). Our results also imply that if M has no conjugate points, then immersions of M into Euclidean space by an orthonormal basis of eigenfunctions with frequencies in (ambda, ambda + 1] are embeddings for all {ambda} sufficiently large.                                                                                                                                                                                                                                                                                                                                                                                
9786   In this paper, we study the two-point Weyl La

In [20]:
id_list = ["1602.00730"]

In [46]:
import src.embedding as embedding
import src.search as search
import importlib
from src.storage import Fetch
from src.cleaning import TextCleaner
from src.embedding import Embedder
from src.search import Search

importlib.reload(embedding)
importlib.reload(search)

<module 'search' from 'c:\\Users\\Leems\\Desktop\\Coding\\Projects\\Fritz\\search.py'>

In [47]:
## Fetch metadata of input
getter = Fetch()
into_cleaner = getter.transform(X=id_list)

In [48]:
cleaner = TextCleaner()

into_embedder = cleaner.transform(into_cleaner)

In [49]:
embedder = Embedder(model_name="allenai-specter")
into_search = embedder.transform(into_embedder)

In [52]:
search = Search(path_to_library="./data/libraries/APSP_50_allenai-specter/")

search.transform(X=into_search).id.to_list()

['1602.00730v1', '1411.0658v3', '1905.05136v3', '1103.1276v4', '2003.04597v2']

In [54]:
from sklearn.pipeline import Pipeline

pipe = Pipeline(
    [
        ("fetch", Fetch()),
        ("clean", TextCleaner()),
        ("embed", Embedder(model_name="allenai-specter")),
        ("search", Search(path_to_library="./data/libraries/APSP_50_allenai-specter/")),
    ]
)


pipe.transform(X=id_list)

title  ...                      msc_tags
38787  C-infinity Scaling Asymptotics for the Spectra...  ...                          None
39127  Scaling Limit for the Kernel of the Spectral P...  ...                          None
9786   A logarithmic improvement in the two-point Wey...  ...                       [35P20]
49609  The blowup along the diagonal of the spectral ...  ...  [58J50, 35J15, 33C45, 32C05]
14857  Growth of high $L^p$ norms for eigenfunctions:...  ...                          None

[5 rows x 5 columns]